In [ ]:
!pip install geopandas

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 14.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.1/16.1 MB 64.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.7/7.7 MB 72.4 MB/s eta 0:00:00


In [ ]:
import geopandas as gpd
f="/content/SHAPEFILE_LV95_LN02/swissBOUNDARIES3D_1_3_TLM_KANTONSGEBIET.shp"
shapes = gpd.read_file(f)
shapes.geometry=shapes.geometry.simplify(0.5)

In [ ]:
import pyproj
from shapely.ops import transform

lv03 = pyproj.CRS('EPSG:21781')
wgs84 = pyproj.CRS('EPSG:4326')
project = pyproj.Transformer.from_crs(lv03, wgs84, 
                                          always_xy=True).transform

for i, shape in shapes.iterrows():
    if shape.geometry is not None:
        shape.geometry = transform(project, shape.geometry)
        shapes.iloc[i] = shape

In [ ]:
gdf=gpd.GeoDataFrame(columns=shapes.columns)

for i, shape in shapes.iterrows():
  if shape.geometry is not None:
    if shape.NAME in gdf.NAME.values:
      available_geometry = gdf.loc[gdf.NAME == shape.NAME,   
                                        'geometry'].geometry.values
      gdf.loc[gdf.NAME == shape.NAME, 'geometry'] =available_geometry.union(shape.geometry)
    else:
      gdf = gdf.append(shape)
gdf=gdf.drop(columns=['KT_TEIL'])

<ipython-input-7-0b998da5f72c>:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  gdf = gdf.append(shape)
<ipython-input-7-0b998da5f72c>:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  gdf = gdf.append(shape)
<ipython-input-7-0b998da5f72c>:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  gdf = gdf.append(shape)
<ipython-input-7-0b998da5f72c>:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  gdf = gdf.append(shape)
<ipython-input-7-0b998da5f72c>:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  gdf = gdf.append(shape)
<ipython-input-7-0b998da5f72c>

In [ ]:
import pandas as pd

In [ ]:
import plotly.express as px

In [ ]:
data

id Parlament                                         OGD Portal  \
1    1        AG            https://www.ag.ch/de/themen/datenportal   
2    2        AR                                                NaN   
3    3        AI                                                NaN   
4    4        BL                                                NaN   
5    5        BS                         https://www.opendata.bs.ch   
0    6        BE  https://opendata.swiss/en/organization/kanton-...   
6    7        FR  https://opendata.swiss/de/organization/kanton_...   
7    8        GE  https://opendata.swiss/en/organization/canton-...   
8    9        GL  https://opendata.swiss/de/organization/kanton-...   
9   10        GR  https://opendata.swiss/de/organization/kanton-...   
10  11        JU                                    nicht vorhanden   
11  12        LU                             https://www.lustat.ch/   
12  13        NE                                    nicht vorhanden   
13  14        NW                                    nicht vorhanden   
14  15        OW                                    nicht vorhanden   
16  16        SH                         https://data.sh.ch/katalog   
17  17        SZ                                https://data.sz.ch/   
18  18        SO                                                NaN   
15  19        SG                           https://www.daten.sg.ch/   
19  20        TG                                https://data.tg.ch/   
20  21        TI                                                NaN   
21  22        UR                                                NaN   
23  23        VS                                                NaN   
22  24        VD                                                NaN   
24  25        ZG                                                NaN   
25  26        ZH                                                NaN   

                                  OGD Parlamentsdaten  Parlamentsmitglieder  \
1                                                 NaN                     3   
2                                                 NaN                     2   
3                                                 NaN                     2   
4                                                 NaN                     2   
5                                                 NaN                     2   
0                                                 NaN                     2   
6                                                 NaN                     2   
7                                                 NaN                     2   
8                                                 NaN                     2   
9                                                 NaN                     2   
10                                                NaN                     2   
11                                                NaN                     3   
12                                                NaN                     2   
13                                                NaN                     2   
14                                                NaN                     2   
16                                                NaN                     2   
17                                                NaN                     2   
18                                                NaN                     2   
15                                                NaN                     2   
19  https://data.tg.ch/explore/dataset/sk-stat-75/...                     1   
20                                                NaN                     2   
21                                                NaN                     3   
23                                                NaN                     2   
22                                                NaN                     2   
24                                                NaN                     2   
25  https://opendata.swiss/de/da

In [36]:
data_file = '/content/liste_kantone_map.csv'
data = pd.read_csv(data_file)
data = data.sort_values(by = ["id"])

data['Kommissionen'] = [0 if d != d else d for d in data['Kommissionen']]

gdf = gdf.sort_values(by = ["NAME"])

fig = px.choropleth_mapbox(data, geojson=gdf.geometry,
                           locations=gdf.index,
                           color='Kommissionen',
                           hover_name = 'Parlament',
                           color_continuous_scale='viridis',
                           mapbox_style="white-bg",
                           zoom=3, 
                           center = {"lat": 46.8, "lon": 8.5},
                           opacity=0.5,
                           )
fig.update_layout(
    title_text = 'Parliamentary Data - Rating 5 Star Open Data')

fig.show()

In [ ]:
data['Parlamentsmitglieder']

1     3.0
2     2.0
3     2.0
4     2.0
5     2.0
0     2.0
6     2.0
7     2.0
8     2.0
9     2.0
10    2.0
11    3.0
12    2.0
13    2.0
14    2.0
16    2.0
17    2.0
18    2.0
15    2.0
19    1.0
20    2.0
21    3.0
23    2.0
22    2.0
24    2.0
25    0.0
Name: Parlamentsmitglieder, dtype: float64

Nachfolgend der Ablauf, die Daten zu laden...

In [ ]:
!curl https://data.geo.admin.ch/ch.swisstopo.swissboundaries3d/swissboundaries3d_2022-05/swissboundaries3d_2022-05_2056_5728.shp.zip --output data.zip

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 33.6M  100 33.6M    0     0  25.1M      0  0:00:01  0:00:01 --:--:-- 25.2M


In [ ]:
!unzip data.zip

Archive:  data.zip
 extracting: SHAPEFILE_LV95_LN02/swissBOUNDARIES3D_1_3_TLM_BEZIRKSGEBIET.cpg  
  inflating: SHAPEFILE_LV95_LN02/swissBOUNDARIES3D_1_3_TLM_BEZIRKSGEBIET.dbf  
  inflating: SHAPEFILE_LV95_LN02/swissBOUNDARIES3D_1_3_TLM_BEZIRKSGEBIET.prj  
  inflating: SHAPEFILE_LV95_LN02/swissBOUNDARIES3D_1_3_TLM_BEZIRKSGEBIET.shp  
  inflating: SHAPEFILE_LV95_LN02/swissBOUNDARIES3D_1_3_TLM_BEZIRKSGEBIET.shx  
 extracting: SHAPEFILE_LV95_LN02/swissBOUNDARIES3D_1_3_TLM_HOHEITSGEBIET.cpg  
  inflating: SHAPEFILE_LV95_LN02/swissBOUNDARIES3D_1_3_TLM_HOHEITSGEBIET.dbf  
  inflating: SHAPEFILE_LV95_LN02/swissBOUNDARIES3D_1_3_TLM_HOHEITSGEBIET.prj  
  inflating: SHAPEFILE_LV95_LN02/swissBOUNDARIES3D_1_3_TLM_HOHEITSGEBIET.shp  
 extracting: SHAPEFILE_LV95_LN02/swissBOUNDARIES3D_1_3_TLM_HOHEITSGEBIET.shp.CVT05050.12184.2840.sr.lock  
  inflating: SHAPEFILE_LV95_LN02/swissBOUNDARIES3D_1_3_TLM_HOHEITSGEBIET.shx  
 extracting: SHAPEFILE_LV95_LN02/swissBOUNDARIES3D_1_3_TLM_HOHEITSGRENZE.cpg  
  inf